In [46]:
import glob
import os

import pandas as pd
import pyproj
import xarray as xr

# Base directory for data used in notebook
DATA_DIR = "../data/air"

# Meaningful column names for each weather parameter, taken from:
# https://www.dmi.dk/fileadmin/Rapporter/2024/DMIRep24-08.pdf
COL_NAMES = {
    "Station": "station_id",
    "Year": "year",
    "Month": "month",
    "Day": "day",
    "Hour(utc)": "hour",
    "101": "mean_air_temp_degc",
    "112": "absolute_max_air_temp_last_hour_degc",
    "113": "absolute_max_air_temp_variable_period_degc",
    "122": "absolute_min_air_temp_last_hour_degc",
    "123": "absolute_min_air_temp_variable_degc",
    "201": "mean_relative_humidity_perc",
    "301": "mean_wind_speed_ms",
    "305": "highest_3sec_wind_speed_ms",
    "365": "mean_wind_direction_last_10min_deg",
    "371": "mean_wind_direction_last_hour_deg",
    "401": "air_pressure_at_msl_hpa",
    "504": "accumulated_sunshine_duration_last_hour_hrs",
    "550": "mean_incoming_radiation_last_hour_wm2",
    "601": "accumulated_precipitation_last_hour_mm",
    "603": "accumulated_sunshine_duration_last_12hour_hrs",
    "609": "accumulated_sunshine_duration_last_24hour_hrs",
    "801": "cloud_cover_perc",
}

# Metadata for resulting dataset
GLOBAL_ATTRS = {
    "author": "Jensen, C. D.",
    "institution": "Danish Meteorological Institute (DMI)",
    "projection": "3413",
    "title": "Weather Observations from Greenland 1958-2023",
    "version": "08 February 2024",
    "data_description": "https://www.dmi.dk/fileadmin/Rapporter/2024/DMIRep24-08.pdf",
}
VAR_ATTRS = {
    "x": {
        "description": "x coordinate of projection",
        "units": "metres",
    },
    "y": {
        "description": "y coordinate of projection",
        "units": "metres",
    },
    "glacier_code": {
        "description": "Initials of glacier name",
    },
    "station_id": {
        "description": "6-digit station number",
    },
    "height": {
        "description": "Height of weather station above mean sea level",
        "units": "metres",
    },
    "t_monthly": {
        "description": "Monthly mean of hourly mean air temperature, measured 2m above ground",
        "units": "degrees celcius",
    },
    "t_anomalies": {
        "description": "Anomalies in monthly mean air temperature calculated relative to a 1988-2024 baseline",
        "units": "degrees celcius",
    },
}

# Collect weather station data files and load station metadata
files = [f for f in glob.glob(f"{DATA_DIR}/*00.csv")]
station_details = pd.read_excel(f"{DATA_DIR}/Station_details.xlsx")

# To temporarily store pre-concatenated monthly datasets
t_ds = []

# Process weather data for each station in turn
for f in files:
    # Extract station metadata
    station_id = int(os.path.splitext(os.path.basename(f))[0])
    station_meta = (
        station_details.loc[station_details["Station number"] == station_id]
        .sort_values(by="Start date")
        .iloc[-1]
    )
    station_height = station_meta.Height

    # Transform coords from WGS84 to projected (EPSG:3413)
    transformer = pyproj.Transformer.from_crs("EPSG:4326", "EPSG:3413")
    station_lat, station_lon = transformer.transform(
        station_meta.Latitude, station_meta.Longitude
    )

    # Generate glacier code based on which file is being processed -
    # requires knowledge of which file is being used for which site
    glacier = "DJ" if station_id == 433900 else "UI"

    # Load weather data, add meaningful labels, and drop empty columns
    air_df = pd.read_csv(f, delimiter=";")
    air_df = air_df.rename(columns=COL_NAMES)
    air_df = air_df.dropna(axis="columns", how="all")

    # Construct and set datetime index from individual date and time components
    air_df["time"] = pd.to_datetime(air_df[["year", "month", "day", "hour"]])
    air_df = air_df.set_index("time")

    # Convert DataFrame to xarray.Dataset
    air_ds = air_df.to_xarray()

    # Define baseline period - manually chosen here as the period of overlap
    # between data from both stations
    baseline = slice("1988-01-01", "2024-01-01")

    # Calculate monthly average, baseline average, and time series anomalies
    t_monthly = air_ds.mean_air_temp_degc.resample(time="1MS").mean()
    t_baseline = t_monthly.sel(time=baseline).groupby("time.month").mean()
    t_anomalies = t_monthly.groupby("time.month") - t_baseline

    # Merge mean and anomalies into single Dataset
    t_monthly = t_monthly.to_dataset(name="t_monthly")
    t_anomalies = t_anomalies.drop_vars("month").to_dataset(name="t_anomalies")
    _t_ds = xr.combine_by_coords([t_monthly, t_anomalies])

    # Assign station metadata and coordinate/variable attributes
    _t_ds = _t_ds.assign_coords(
        station_id=("station_id", [station_id], VAR_ATTRS["station_id"]),
        glacier_code=("station_id", [glacier], VAR_ATTRS["glacier_code"]),
        x=("station_id", [station_lat], VAR_ATTRS["x"]),
        y=("station_id", [station_lon], VAR_ATTRS["y"]),
        height=("station_id", [station_height], VAR_ATTRS["height"]),
    )
    _t_ds["t_monthly"] = _t_ds.t_monthly.assign_attrs(VAR_ATTRS["t_monthly"])
    _t_ds["t_anomalies"] = _t_ds.t_anomalies.assign_attrs(VAR_ATTRS["t_anomalies"])
    t_ds.append(_t_ds)

# Merge Datasets station-wise, assign global attributes, and write to disk
t_ds = xr.combine_by_coords(t_ds)
t_ds = t_ds.assign_attrs(GLOBAL_ATTRS)
# t_ds.to_netcdf(f"{DATA_DIR}/air_temp_monthly_1980_2024.nc")

t_ds

<xarray.Dataset> Size: 21kB
Dimensions:       (station_id: 2, time: 519)
Coordinates:
  * time          (time) datetime64[ns] 4kB 1980-11-01 1980-12-01 ... 2024-01-01
  * station_id    (station_id) int32 8B 433900 435100
    glacier_code  (station_id) <U2 16B 'DJ' 'UI'
    x             (station_id) float64 16B 8.355e+05 5.363e+05
    y             (station_id) float64 16B -1.964e+06 -2.377e+06
    height        (station_id) float64 16B 70.0 12.0
Data variables:
    t_anomalies   (station_id, time) float64 8kB -4.666 -7.972 ... -2.358 1.985
    t_monthly     (station_id, time) float64 8kB -13.57 -20.1 ... -9.669 -6.776
Attributes:
    author:            Jensen, C. D.
    institution:       Danish Meteorological Institute (DMI)
    projection:        3413
    title:             Weather Observations from Greenland 1958-2023
    version:           08 February 2024
    data_description:  https://www.dmi.dk/fileadmin/Rapporter/2024/DMIRep24-0...

In [2]:
import matplotlib.pyplot as plt
import xarray as xr
from matplotlib.dates import DateFormatter, YearLocator
from matplotlib.gridspec import GridSpec
from matplotlib.offsetbox import AnchoredText

PLOT_SETTINGS = {
    "DJ": {
        "colour": [(0.122, 0.467, 0.706, 1.0), (0.122, 0.467, 0.706, 0.25)],
        "label": "Daugaard-Jensen",
    },
    "UI": {
        "colour": [(1.0, 0.498, 0.055, 1.0), (1.0, 0.498, 0.055, 0.25)],
        "label": "Uunartit Islands",
    },
}

# Global plot settings
plt.rcParams["figure.dpi"] = 1000
plt.rcParams["font.family"] = "Times New Roman"
plt.rcParams["font.size"] = 18
plt.rcParams["axes.labelsize"] = 18
plt.rcParams["xtick.labelsize"] = 18
plt.rcParams["ytick.labelsize"] = 18

# Create figure and axes
fig = plt.figure(figsize=(16, 12))
gs = GridSpec(nrows=2, ncols=2, width_ratios=[1, 2], height_ratios=[1, 1])
ax0 = fig.add_subplot(gs[0, 0])
ax1 = fig.add_subplot(gs[0, 1:])
ax2 = fig.add_subplot(gs[1, 0])
ax3 = fig.add_subplot(gs[1, 1:])
ax = [ax0, ax1, ax2, ax3]

# Read temperature time series produced above from disk
t_ds = xr.open_dataset(f"{DATA_DIR}/air_temp_monthly_1980_2024.nc")

# Define temporal slices for each axis
col0_slice = slice("1985-01-01", "2010-01-01")
col1_slice = slice("2010-01-01", "2024-01-01")

# Plot data for each glacier in turn
for glacier, t_ds_glacier in t_ds.groupby("glacier_code"):
    # Plot data on each axis in turn
    for j, slice_ in enumerate([col0_slice, col1_slice]):
        # Subset dataset by temporal slice of current column
        t_ds_glacier_slice = t_ds_glacier.sel(time=slice_)

        # Plot monthly mean surface air temperature
        ax[j].plot(
            t_ds_glacier_slice.time,
            t_ds_glacier_slice.t_monthly.squeeze(),
            color=PLOT_SETTINGS[glacier]["colour"][0],
            linewidth=2.5,
            label=PLOT_SETTINGS[glacier]["label"],
        )
        # Plot anomalies of monthly mean surface air temperature
        ax[j + 2].plot(
            t_ds_glacier_slice.time,
            t_ds_glacier_slice.t_anomalies.squeeze(),
            color=PLOT_SETTINGS[glacier]["colour"][0],
            linewidth=2.5,
            label=PLOT_SETTINGS[glacier]["label"],
        )

# Set y-axis range to fit data and adds label
ax[0].set_ylabel("Surface air temperature [\N{DEGREE SIGN}C]", labelpad=20)
ax[0].set_ylim(bottom=-20, top=10)
ax[1].set_ylim(bottom=-20, top=10)
ax[2].set_ylabel("Surface air temperature anomaly [\N{DEGREE SIGN}C]", labelpad=20)
ax[2].set_ylim(bottom=-8, top=10)
ax[3].set_ylim(bottom=-8, top=10)

# Set x-axis range to fit data
ax[0].set_xlim(pd.to_datetime("1985-01-01"), pd.to_datetime("2010-01-01"))
ax[1].set_xlim(pd.to_datetime("2010-01-01"), pd.to_datetime("2024-01-01"))
ax[2].set_xlim(pd.to_datetime("1985-01-01"), pd.to_datetime("2010-01-01"))
ax[3].set_xlim(pd.to_datetime("2010-01-01"), pd.to_datetime("2024-01-01"))

# Set x-axis tick frequency and format (major)
ax[0].xaxis.set_major_locator(YearLocator(base=5))
ax[2].xaxis.set_major_locator(YearLocator(base=5))
ax[2].xaxis.set_major_formatter(DateFormatter("%Y"))
ax[3].xaxis.set_major_formatter(DateFormatter("%Y"))

# Set x-axis tick frequency (minor)
ax[0].xaxis.set_minor_locator(YearLocator(1))
ax[1].xaxis.set_minor_locator(YearLocator(1))
ax[2].xaxis.set_minor_locator(YearLocator(1))
ax[3].xaxis.set_minor_locator(YearLocator(1))

# Rotate x-axis tick labels
ax[2].tick_params(axis="x", rotation=70)
ax[3].tick_params(axis="x", rotation=70)

# Disable x- and y-axis tick labels to avoid repetition
ax[0].tick_params(labelbottom=False)
ax[1].tick_params(labelbottom=False, labelleft=False)
ax[3].tick_params(labelleft=False)

# Remove whitespace around data on plot
ax[0].margins(x=0)
ax[1].margins(x=0)
ax[2].margins(x=0)
ax[3].margins(x=0)

# Draw horizontal line at y=0
ax[2].axhline(y=0, c="black", alpha=0.7, linewidth=0.7, zorder=1, linestyle=(0, (6, 8)))
ax[3].axhline(y=0, c="black", alpha=0.7, linewidth=0.7, zorder=1, linestyle=(0, (6, 8)))

# Add plot labels and advance/retreat text
ax[0].add_artist(
    AnchoredText(
        "(a)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)
ax[1].add_artist(
    AnchoredText(
        "(b)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)
ax[2].add_artist(
    AnchoredText(
        "(c)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)
ax[3].add_artist(
    AnchoredText(
        "(d)",
        loc="upper left",
        borderpad=0.1,
        prop=dict(size=18, family="Times New Roman", weight="semibold", c="black"),
        frameon=False,
    )
)

# # Draw legend
# ax[0].legend(
#     frameon=False,
#     loc="lower left",
#     fontsize=16,
#     markerscale=2,
#     scatterpoints=1,
# )

# Add gridlines
ax[0].grid(
    True,
    which="major",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)
ax[1].grid(
    True,
    which="both",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)
ax[2].grid(
    True,
    which="major",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)
ax[3].grid(
    True,
    which="both",
    axis="both",
    c="gray",
    linestyle=":",
    linewidth=0.5,
    alpha=0.8,
    zorder=0,
)

plt.tight_layout()
# plt.savefig(
#     "../img/air_temperature_1985_2023_time-series.png",
#     dpi=fig.dpi,
#     bbox_inches="tight",
# )
plt.show()